In [39]:
from rdkit import Chem
from rdkit.Chem import Descriptors
import pandas as pd
import os
os.environ['R_HOME'] = 'C:\Programming\R\R-4.4.2'

In [40]:
class MolecularFeatureExtractor:
    def __init__(self):
        self.descriptors = [desc[0] for desc in Descriptors._descList]

    def extract_molecular_features(self, smiles_list):
        features_dict = {desc: [] for desc in self.descriptors}

        for smiles in smiles_list:
            mol = Chem.MolFromSmiles(smiles)
            if mol:
                for descriptor_name in self.descriptors:
                    descriptor_function = getattr(Descriptors, descriptor_name)
                    try:
                        features_dict[descriptor_name].append(descriptor_function(mol))
                    except:
                        features_dict[descriptor_name].append(None)
            else:
                for descriptor_name in self.descriptors:
                    features_dict[descriptor_name].append(None)

        return pd.DataFrame(features_dict)

In [41]:
# data load
df = pd.read_csv(r'C:\Programming\Github\EGCN\data\esol.csv')

smiles_list = df['smiles'].tolist()
target = df['logp']

print(smiles_list[:5])
print(target[:5])

['OCC3OC(OCC2OC(OC(C#N)c1ccccc1)C(O)C(O)C2O)C(O)C(O)C3O', 'Cc1occc1C(=O)Nc2ccccc2', 'CC(C)=CCCC(C)=CC(=O)', 'c1ccc2c(c1)ccc3c2ccc4c5ccccc5ccc43', 'c1ccsc1']
0   -0.77
1   -3.30
2   -2.06
3   -7.87
4   -1.33
Name: logp, dtype: float64


In [42]:
# 분자 특성 추출
extractor = MolecularFeatureExtractor()
features_df = extractor.extract_molecular_features(smiles_list)

features_df['target'] = target

initial_feature_count = features_df.shape[1] - 1  # logvp 열 제외
print("초기 변수 개수:", initial_feature_count)

초기 변수 개수: 208


# 결측치 처리

In [43]:
# 1. 결측치가 있는 특성 제거
cleaned_features_df = features_df.dropna(axis=1)
cleaned_feature_count = cleaned_features_df.shape[1] - 1  # logvp 열 제외
print("결측치가 있는 변수 제거 후 남은 변수 개수:", cleaned_feature_count)
print("제거된 변수 개수 (결측치):", initial_feature_count - cleaned_feature_count)

missing_ratio = features_df.isnull().mean().sort_values(ascending=False)
print("결측값 비율:\n", missing_ratio[missing_ratio > 0])

결측치가 있는 변수 제거 후 남은 변수 개수: 208
제거된 변수 개수 (결측치): 0
결측값 비율:
 Series([], dtype: float64)


In [44]:
cleaned_features_df

MaxEStateIndex  MinEStateIndex  MaxAbsEStateIndex  MinAbsEStateIndex  \
0          10.253329       -1.701605          10.253329           0.486602   
1          11.724911       -0.145880          11.724911           0.145880   
2          10.020498        0.845090          10.020498           0.845090   
3           2.270278        1.301055           2.270278           1.301055   
4           2.041667        1.712963           2.041667           1.712963   
...              ...             ...                ...                ...   
1123       10.999421       -4.317901          10.999421           1.916667   
1124       11.337508       -0.705457          11.337508           0.123704   
1125        5.174287       -1.984662           5.174287           1.011373   
1126        2.222222        0.884259           2.222222           0.884259   
1127       11.888207       -3.753520          11.888207           0.016420   

           qed    MolWt  HeavyAtomMolWt  ExactMolWt  NumValenceElectrons  \
0     0.217518  457.432         430.216  457.158411                  178   
1     0.811283  201.225         190.137  201.078979                   76   
2     0.343706  152.237         136.109  152.120115                   62   
3     0.291526  278.354         264.242  278.109550                  102   
4     0.448927   84.143          80.111   84.003371                   26   
...        ...      ...             ...         ...                  ...   
1123  0.523506  197.381         196.373  195.890224                   44   
1124  0.293876  219.266         206.162  219.067762                   80   
1125  0.506070  246.359         231.239  245.997179                   74   
1126  0.444441   72.151          60.055   72.093900                   32   
1127  0.386625  365.964         356.892  363.899256                  106   

      NumRadicalElectrons  ...  fr_sulfonamd  fr_sulfone  fr_term_acetylene  \
0                       0  ...             0           0                  0   
1                       0  ...             0           0                  0   
2                       0  ...             0           0                  0   
3                       0  ...             0           0                  0   
4                       0  ...             0           0                  0   
...                   ...  ...           ...         ...                ...   
1123                    0  ...             0           0                  0   
1124                    0  ...             0           0                  0   
1125                    0  ...             0           0                  0   
1126                    0  ...             0           0                  0   
1127                    0  ...             0           0                  0   

      fr_tetrazole  fr_thiazole  fr_thiocyan  fr_thiophene  fr_unbrch_alkane  \
0                0            0            0             0                 0   
1                0            0            0             0                 0   
2                0            0            0             0                 0   
3                0            0            0             0                 0   
4                0            0            0             1                 0   
...            ...          ...          ...           ...               ...   
1123             0            0            0             0                 0   
1124             0            0            0             0                 0   
1125             0            0            0             0                 2   
1126             0            0            0             0                 0   
1127             0            0            0             0                 0   

      fr_urea  target  
0           0  -0.770  
1           0  -3.300  
2           0  -2.060  
3           0  -7.870  
4           0  -1.330  
...       ...     ...  
1123        0  -1.710  
1124        0   0.106  
1125        0  -3.091  
1126  

In [45]:
# 표준화된 데이터에서 각 특성의 분산 계산
feature_variances = cleaned_features_df.var()
print(sorted(feature_variances))

# 분산 출력
print("각 특징의 분산:")
print(feature_variances)

# 분산 요약 통계 확인
print("\n분산 요약 통계:")
print(feature_variances.describe())

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0008865248226950355, 0.0008865248226950355, 0.0008865248226950357, 0.0008865248226950358, 0.0008865248226950358, 0.0008865248226950359, 0.0017714763981448273, 0.0017714763981448273, 0.002654854726349374, 0.002654854726349374, 0.0026548547263493746, 0.0035366598073086775, 0.0035366598073086775, 0.004416891641022736, 0.005295550227491549, 0.00529555022749155, 0.00529555022749155, 0.006172635566715123, 0.006172635566715123, 0.006172635566715123, 0.007048147658693451, 0.009665244451156966, 0.010534463554154319, 0.013132681379674905, 0.013995607493691277, 0.014042804911048602, 0.014146639229234708, 0.014856960360462414, 0.014951355195177053, 0.015172369730968027, 0.01754485327896191, 0.019959863712542863, 0.022261390926740256, 0.023261038804962726, 0.023332101692019096, 0.02439162529026412, 0.027940871075534748, 0.029259252267049275, 0.031866909576041325, 0.03646157815577665, 0.0530467506151396

In [46]:
# 2. 분산이 0인 특성 제거
variance_threshold = 0
low_variance_features2 = cleaned_features_df.loc[:, cleaned_features_df.var() > variance_threshold]
low_variance_feature_count2 = low_variance_features2.shape[1] - 1  # logvp 열 제외
print("분산 기준 적용 후 남은 변수 개수:", low_variance_feature_count2)
print("제거된 변수 개수 (분산이 0인 변수):", cleaned_feature_count - low_variance_feature_count2)

분산 기준 적용 후 남은 변수 개수: 189
제거된 변수 개수 (분산이 0인 변수): 19


In [47]:
print(low_variance_features2.shape)
print(low_variance_features2.head())

(1128, 190)
   MaxEStateIndex  MinEStateIndex  MaxAbsEStateIndex  MinAbsEStateIndex  \
0       10.253329       -1.701605          10.253329           0.486602   
1       11.724911       -0.145880          11.724911           0.145880   
2       10.020498        0.845090          10.020498           0.845090   
3        2.270278        1.301055           2.270278           1.301055   
4        2.041667        1.712963           2.041667           1.712963   

        qed    MolWt  HeavyAtomMolWt  ExactMolWt  NumValenceElectrons  \
0  0.217518  457.432         430.216  457.158411                  178   
1  0.811283  201.225         190.137  201.078979                   76   
2  0.343706  152.237         136.109  152.120115                   62   
3  0.291526  278.354         264.242  278.109550                  102   
4  0.448927   84.143          80.111   84.003371                   26   

   MaxPartialCharge  ...  fr_pyridine  fr_sulfide  fr_sulfonamd  fr_sulfone  \
0          0.188266

# 3. 데이터 스크리닝 (SIS & ISIS)

In [48]:
X_train = low_variance_features2.drop(columns = 'target')
y_train = low_variance_features2['target']

print(X_train.shape)
print(y_train.shape)

(1128, 189)
(1128,)


In [49]:
# 스케일링
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
scaler.fit(X_train)

X_train_scaling = scaler.transform(X_train)

In [50]:
X_train_scaling[0]

array([ 5.43888515e-01, -1.17419817e+00,  5.43888515e-01, -1.75655892e-03,
       -2.24871416e+00,  2.46848464e+00,  2.40476640e+00,  2.47851455e+00,
        2.93164732e+00,  1.28050018e-01, -5.92972500e-01,  5.45299742e-01,
        1.39464377e-01, -8.84901825e-01, -6.51213168e-01, -1.81866036e-01,
       -4.69796406e-01, -5.80740747e-01,  1.30797929e+00, -1.53348600e+00,
        4.02558501e-01, -1.76069133e+00, -6.37592511e-01, -1.17481651e+00,
       -1.78178807e+00,  1.55928089e+00,  2.78950301e+00,  2.34689694e+00,
        2.07642484e+00,  2.73695764e+00,  2.32291387e+00,  1.95147412e+00,
        2.00127898e+00,  1.46197001e+00,  1.69690073e+00,  1.20472990e+00,
        1.27998887e+00,  8.85735730e-01, -8.02578186e-01, -4.12432632e-02,
        3.01622639e+00,  2.64440136e+00,  3.44402258e-02,  2.46419180e+00,
        6.63750831e+00,  6.68220818e+00,  4.14097009e+00, -4.28701190e-01,
       -3.56004607e-01, -5.37778871e-01, -6.13710564e-01, -4.98640646e-01,
        1.27803643e+00, -

In [51]:
# Python to R type
from rpy2.robjects import r
from rpy2.robjects import pandas2ri
from rpy2.robjects import FloatVector

pandas2ri.activate()

X_train_scaling = r['as.matrix'](X_train_scaling)

y_train = FloatVector(y_train)

nfolds = 10
nfolds = FloatVector([nfolds])[0]

nsis = 100
nsis = FloatVector([nsis])[0]

seed = 9
seed = FloatVector([seed])[0]

In [52]:
from rpy2.robjects.packages import importr
SIS = importr('SIS')
import sys
import io

# R 출력이 발생할 때 UTF-8 오류를 방지하기 위해, 표준 출력을 임시로 바꿔서 처리할 수 있습니다.
#r('Sys.setlocale("LC_ALL", "C.UTF-8")')

# model1 = SIS(...)
model1 = SIS.SIS(
    X_train_scaling,
    y_train,
    family="gaussian",
#    penalty="MCP",
    tune="cv",
    nfolds=nfolds,
    nsis=nsis,
    varISIS="aggr",
    seed=seed,
    q=0.95,
    standardize=False)
#model1

# # 22. R: `model2 = SIS(...)`
# model2 = SIS.SIS(
#     X_train_scaling,
#     y_train,
#     family="gaussian",
#     penalty="lasso",
#     tune="cv",
#     nfolds=nfolds,
#     nsis=nsis,
#     varISIS="aggr",
    
#     perm=True,
#     q=0.95,
    
#     seed=seed,
#     standardize=False
# )


Iter 1 , screening:  6 7 8 9 11 12 14 15 18 19 20 21 23 25 26 27 28 29 30 31 32 33 34 35 36 37 38 41 42 44 55 56 58 60 66 67 71 75 76 77 78 83 84 86 89 90 92 97 101 102 103 105 108 110 112 114 118 119 120 
Iter 1 , selection:  11 12 14 18 19 25 26 34 35 36 37 55 56 58 60 75 76 77 83 86 89 101 103 105 108 114 118 119 
Iter 1 , conditional-screening:  1 3 6 7 8 9 10 13 27 28 29 30 33 39 45 49 50 51 64 68 69 71 79 90 92 93 97 102 104 111 113 115 117 120 125 126 127 128 144 158 161 162 171 173 
Iter 2 , screening:  1 3 6 7 8 9 10 11 12 13 14 18 19 25 26 27 28 29 30 33 34 35 36 37 39 45 49 50 51 55 56 58 60 64 68 69 71 75 76 77 79 83 86 89 90 92 93 97 101 102 103 104 105 108 111 113 114 115 117 118 119 120 125 126 127 128 144 158 161 162 171 173 
Iter 2 , selection:  1 10 12 13 14 18 19 25 34 45 49 50 55 56 60 68 69 83 86 89 97 101 108 114 117 119 125 144 161 162 173 
Iter 2 , conditional-screening:  3 6 7 8 11 15 22 24 33 36 38 42 51 61 63 64 66 67 74 75 76 90 92 105 107 110 111 113 115 11

In [53]:
print(str(model1))

$sis.ix0
 [1]   6   7   8   9  11  12  14  15  18  19  20  21  23  25  26  27  28  29  30
[20]  31  32  33  34  35  36  37  38  41  42  44  55  56  58  60  66  67  71  75
[39]  76  77  78  83  84  86  89  90  92  97 101 102 103 105 108 110 112 114 118
[58] 119 120

$ix
 [1]   1  10  12  13  14  15  18  19  24  25  42  49  50  51  52  57  58  60  63
[20]  67  69  71  74  75  77  82  83  89  93  97 101 108 110 117 119 125 127 133
[39] 142 143 146 156 161 162 165 166 170 173 185

$coef.est
 (Intercept)           X1          X10          X12          X13          X14 
-3.050101950  0.244702437  0.562515665  0.405350786 -0.640750614  0.002342274 
         X15          X18          X19          X24          X25          X42 
 0.090573753  0.153303909 -0.475063649  0.103964756  0.301615734 -0.358140692 
         X49          X50          X51          X52          X57          X58 
-0.158451149 -0.176576356  0.218774806  0.142080612  0.132724522  0.097263370 
         X60          X63         

In [54]:
import numpy as np
a = np.array(model1.rx2('ix'))
len(a)


49

In [55]:
low_variance_features2

MaxEStateIndex  MinEStateIndex  MaxAbsEStateIndex  MinAbsEStateIndex  \
0          10.253329       -1.701605          10.253329           0.486602   
1          11.724911       -0.145880          11.724911           0.145880   
2          10.020498        0.845090          10.020498           0.845090   
3           2.270278        1.301055           2.270278           1.301055   
4           2.041667        1.712963           2.041667           1.712963   
...              ...             ...                ...                ...   
1123       10.999421       -4.317901          10.999421           1.916667   
1124       11.337508       -0.705457          11.337508           0.123704   
1125        5.174287       -1.984662           5.174287           1.011373   
1126        2.222222        0.884259           2.222222           0.884259   
1127       11.888207       -3.753520          11.888207           0.016420   

           qed    MolWt  HeavyAtomMolWt  ExactMolWt  NumValenceElectrons  \
0     0.217518  457.432         430.216  457.158411                  178   
1     0.811283  201.225         190.137  201.078979                   76   
2     0.343706  152.237         136.109  152.120115                   62   
3     0.291526  278.354         264.242  278.109550                  102   
4     0.448927   84.143          80.111   84.003371                   26   
...        ...      ...             ...         ...                  ...   
1123  0.523506  197.381         196.373  195.890224                   44   
1124  0.293876  219.266         206.162  219.067762                   80   
1125  0.506070  246.359         231.239  245.997179                   74   
1126  0.444441   72.151          60.055   72.093900                   32   
1127  0.386625  365.964         356.892  363.899256                  106   

      MaxPartialCharge  ...  fr_pyridine  fr_sulfide  fr_sulfonamd  \
0             0.188266  ...            0           0             0   
1             0.258698  ...            0           0             0   
2             0.142281  ...            0           0             0   
3            -0.009873  ...            0           0             0   
4            -0.009338  ...            0           0             0   
...                ...  ...          ...         ...           ...   
1123          0.414120  ...            0           0             0   
1124          0.432627  ...            0           1             0   
1125          0.246324  ...            0           1             0   
1126         -0.047395  ...            0           0             0   
1127          0.529073  ...            0           0             0   

      fr_sulfone  fr_term_acetylene  fr_thiazole  fr_thiophene  \
0              0                  0            0             0   
1              0                  0            0             0   
2              0                  0            0             0   
3              0                  0            0             0   
4              0                  0            0             1   
...          ...                ...          ...           ...   
1123           0                  0            0             0   
1124           0                  0            0             0   
1125           0                  0            0             0   
1126           0                  0            0             0   
1127           0                  0            0             0   

      fr_unbrch_alkane  fr_urea  target  
0                    0        0  -0.770  
1                    0        0  -3.300  
2                    0        0  -2.060  
3                    0        0  -7.870  
4                    0        0  -1.330  
...                ...      ...     ...  
1123                 0        0  -1.710  
1124                 0        0   0.106  
1125                 2        0  -3.091  
1126                 0        0  -3.180  
1127                 0        0  -4.522  

[1128 rows x 190 

In [56]:
feature_names = low_variance_features2.drop(columns=['target']).columns
feature_names
feature_selection = feature_names[a]
feature_selection


Index(['MinEStateIndex', 'MinPartialCharge', 'MinAbsPartialCharge',
       'FpDensityMorgan1', 'FpDensityMorgan2', 'FpDensityMorgan3',
       'BCUT2D_CHGHI', 'BCUT2D_CHGLO', 'BalabanJ', 'BertzCT', 'Kappa3',
       'PEOE_VSA14', 'PEOE_VSA2', 'PEOE_VSA3', 'PEOE_VSA4', 'PEOE_VSA9',
       'SMR_VSA1', 'SMR_VSA2', 'SMR_VSA5', 'SlogP_VSA1', 'SlogP_VSA11',
       'SlogP_VSA2', 'SlogP_VSA5', 'SlogP_VSA6', 'SlogP_VSA8', 'EState_VSA2',
       'EState_VSA3', 'EState_VSA9', 'VSA_EState3', 'VSA_EState7',
       'HeavyAtomCount', 'NumAromaticHeterocycles', 'NumHAcceptors',
       'RingCount', 'MolMR', 'fr_Ar_OH', 'fr_C_O_noCOO', 'fr_NH2',
       'fr_allylic_oxid', 'fr_amide', 'fr_azo', 'fr_guanido', 'fr_imide',
       'fr_ketone', 'fr_methoxy', 'fr_nitrile', 'fr_oxazole', 'fr_phenol',
       'fr_thiazole'],
      dtype='object')

In [57]:
ISIS_df = low_variance_features2[list(feature_selection)+['target']]
ISIS_df

MinEStateIndex  MinPartialCharge  MinAbsPartialCharge  FpDensityMorgan1  \
0          -1.701605         -0.393567             0.188266          0.812500   
1          -0.145880         -0.468799             0.258698          1.200000   
2           0.845090         -0.298566             0.142281          1.272727   
3           1.301055         -0.061629             0.009873          0.272727   
4           1.712963         -0.152454             0.009338          1.000000   
...              ...               ...                  ...               ...   
1123       -4.317901         -0.168387             0.168387          1.428571   
1124       -0.705457         -0.342862             0.342862          1.428571   
1125       -1.984662         -0.325040             0.246324          1.250000   
1126        0.884259         -0.065138             0.047395          1.400000   
1127       -3.753520         -0.402377             0.402377          1.105263   

      FpDensityMorgan2  FpDensityMorgan3  BCUT2D_CHGHI  BCUT2D_CHGLO  \
0             1.375000          1.968750      2.475238     -2.425092   
1             1.933333          2.533333      2.102137     -2.025284   
2             1.909091          2.363636      1.860315     -1.944429   
3             0.636364          1.136364      2.059971     -2.093248   
4             1.600000          1.800000      1.581286     -1.392416   
...                ...               ...           ...           ...   
1123          1.571429          1.571429      2.352344     -2.031989   
1124          2.000000          2.357143      2.133809     -2.089621   
1125          1.833333          2.250000      2.142743     -2.153437   
1126          1.600000          1.600000      1.795310     -1.900999   
1127          1.631579          2.105263      2.271357     -2.169120   

      BalabanJ      BertzCT  ...  fr_azo  fr_guanido  fr_imide  fr_ketone  \
0     1.654937   759.662938  ...       0           0         0          0   
1     2.148162   459.484175  ...       0           0         0          0   
2     3.625760   171.311799  ...       0           0         0          0   
3     2.041379  1071.547817  ...       0           0         0          0   
4     3.125000    60.124818  ...       0           0         0          0   
...        ...          ...  ...     ...         ...       ...        ...   
1123  3.541197    58.445472  ...       0           0         0          0   
1124  4.399366   252.564575  ...       0           0         0          0   
1125  3.522395   145.728624  ...       0           0         0          0   
1126  2.539539    14.000000  ...       0           0         0          0   
1127  3.195069   538.576344  ...       0           0         0          0   

      fr_methoxy  fr_nitrile  fr_oxazole  fr_phenol  fr_thiazole  target  
0              0           1           0          0            0  -0.770  
1              0           0           0          0            0  -3.300  
2              0           0           0          0            0  -2.060  
3              0           0           0          0            0  -7.870  
4              0           0           0          0            0  -1.330  
...          ...         ...         ...        ...          ...     ...  
1123           0           0           0          0            0  -1.710  
1124           0           0           0          0            0   0.106  
1125           0           0           0          0            0  -3.091  
1126           0           0           0          0            0  -3.180  
1127           0           0           0          0            0  -4.522  

[1128 rows x 50 columns]

In [58]:
from sklearn.linear_model import ElasticNet
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.feature_selection import RFE

In [59]:
X = ISIS_df.drop(columns=['target'])  # 독립 변수
y = ISIS_df['target']  # 종속 변수

# 데이터 스케일링
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

# 학습 및 테스트 데이터 분리
X_train, X_test, y_train, y_test = train_test_split(X_scaled, y, test_size=0.2, random_state=42)

# ElasticNet 모델과 하이퍼파라미터 범위 설정
elastic_net = ElasticNet(max_iter=5000)
param_grid = {
    'alpha': [0.001, 0.01, 0.1, 1.0, 10.0],  # 정규화 강도
    'l1_ratio': [0.1, 0.3, 0.5, 0.7, 0.9, 1.0]  # L1과 L2 비율
}

# GridSearchCV를 사용하여 최적 하이퍼파라미터 탐색
grid_search = GridSearchCV(
    estimator=elastic_net,
    param_grid=param_grid,
    scoring='neg_mean_squared_error',  # 음의 MSE 사용
    cv=5,  # 5-폴드 교차 검증
    verbose=1,
    n_jobs=-1
)

grid_search.fit(X_train, y_train)

# 최적 하이퍼파라미터로 ElasticNet 모델 생성
best_params = grid_search.best_params_
optimal_elastic_net = ElasticNet(
    alpha=best_params['alpha'],
    l1_ratio=best_params['l1_ratio'],
    max_iter=5000
)

# RFE 실행 (최종적으로 10개의 특성 선택)
num_features = [3, 5, 7, 10, 20]
for i in num_features:
    rfe = RFE(estimator=optimal_elastic_net, n_features_to_select= i)
    rfe.fit(X_train, y_train)

    # RFE로 선택된 특성 이름 확인
    selected_features_indices = rfe.support_
    selected_features_names = X.columns[selected_features_indices]
    print("최종 선택된 특성:", list(selected_features_names))

# # 최종 선택된 특성으로 데이터프레임 생성
# df_final_selected = ISIS_df[selected_features_names.tolist() + ['target']]
# print("최종 데이터프레임:")
# print(df_final_selected.head())

Fitting 5 folds for each of 30 candidates, totalling 150 fits
최종 선택된 특성: ['MinPartialCharge', 'SlogP_VSA2', 'MolMR']
최종 선택된 특성: ['MinPartialCharge', 'FpDensityMorgan1', 'SlogP_VSA2', 'SlogP_VSA6', 'MolMR']
최종 선택된 특성: ['MinPartialCharge', 'FpDensityMorgan1', 'SMR_VSA5', 'SlogP_VSA2', 'SlogP_VSA6', 'HeavyAtomCount', 'MolMR']
최종 선택된 특성: ['MinPartialCharge', 'FpDensityMorgan1', 'FpDensityMorgan3', 'SMR_VSA5', 'SlogP_VSA2', 'SlogP_VSA6', 'HeavyAtomCount', 'NumHAcceptors', 'RingCount', 'MolMR']
최종 선택된 특성: ['MinEStateIndex', 'MinPartialCharge', 'MinAbsPartialCharge', 'FpDensityMorgan1', 'FpDensityMorgan2', 'FpDensityMorgan3', 'BCUT2D_CHGHI', 'SMR_VSA5', 'SlogP_VSA2', 'SlogP_VSA5', 'SlogP_VSA6', 'SlogP_VSA8', 'EState_VSA9', 'VSA_EState7', 'HeavyAtomCount', 'NumAromaticHeterocycles', 'NumHAcceptors', 'RingCount', 'MolMR', 'fr_C_O_noCOO']
